## EPS 109
### Final project: 2D fluid flow through objects.

**Read Me**:

This project is the code representation of what could be found on the pdf below using python.
I took the liberty to extract some text description for each step of the process in order to guide the reader.
https://physics.weber.edu/schroeder/javacourse/LatticeBoltzmann.pdf

I've never taken a class in fluid mechanics, however I want to thank my Data Science Modules department that helped me understand a bit more about fluids and gave me some coding tips and guidance throghout the project.

------

#### Lattice Boltzmann method

Lattice Boltzmann methods (LBM) is a is a fluid simulation method that allow us to simulate fluid density with streaming and collision processes.

LBM can be discretized,meaning that a fluid flow under LBM can be a set of logically separate processes that autonomously progress through time.
being discretized means that we can use a coding language like python to simulate it!


In [1]:
##Please run the following cell
%matplotlib qt
#%matplotlib notebook 
import numpy as np
import copy
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter

metadata = dict(title='My first animation in 2D', artist='Matplotlib',comment='Wakanda is coming.')
writer = FFMpegWriter(fps=15, metadata=metadata)

---------------------------

## Simulation Parameters

Before we can start simulating, we need to define our fluid, and the context its being simulated.
**Rho:** Fluid Density is the mass per unit volume and is denoted by the Greek letter ρ (rho).

In Lattice Boltzmann τ is the timescale of which collisions happen 

In [2]:
#Simulation parameters:
Nx                     = 300    # resolution x-dir
Ny                     = 150    # resolution y-dir
localNy = 80
#Fluid attribute and behavior
rho0                   = 100    # average density
tau                    = 0.6    # collision timescale
#Plot wise
dt                     = 4000   # number of timesteps
# Cylinder boundary
X, Y = np.meshgrid(range(Nx), range(Ny))
cylinder = (X - Nx/4)**2 + (Y - localNy/2)**2 < (localNy/4)**2
cylinder2 = np.copy(cylinder)

#Shift the cylinders so they don't collide.
cylinder = np.roll(cylinder, -10, axis=0)
cylinder2 = np.roll(cylinder2, +60, axis=0)

#### D2Q9 lattice vectors

In the lattice-Boltzmann approach, we discretize both space and time so that only
certain discrete velocity vectors are allowed. In this project, we will use the so-called
D2Q9 lattice in which there are two dimensions and just nine allowed displacement
vectors, shown in the illustration above. One of the allowed displacements is zero,
while the other eight take a molecule from its current site into one of the eight
nearest sites in the square lattice—either horizontally, vertically, or at a 45-degree
diagonal. We can write the nine allowed displacement vectors as $\vec{e_i}$
, where i runs
from 0 through 8 and each $\vec{e_i}$ has x and y components that are −1, 0, or 1, in units of
the lattice spacing, ∆x. If the simulation time step is ∆t, then the allowed velocity
vectors are given by $c \cdot \vec{e_i}$
, where c is an abbreviation for ∆x/∆t.

$\vec{e_0} = (0,0)$

$\vec{e_1} = (1,0) , \vec{e_2} = (0,1) $

$\vec{e_3} = (-1,0) , \vec{e_4} = (0,-1) $

$\vec{e_5} = (1,1) , \vec{e_6} = (-1,1) $

$\vec{e_7} = (-1,-1) , \vec{e_8} = (1,-1) $



In [3]:
NL = 9
idxs = np.arange(NL)
#notice how [cxs[0],cys[0]] is equivalent to e_0 = (0,0)
cxs = np.array([0, 0, 1, 1, 1, 0,-1,-1,-1])
cys = np.array([0, 1, 1, 0,-1,-1,-1, 0, 1])

Our task, now, is to attach probabilities to these nine velocity vectors, to model
the continuous Boltzmann distribution as accurately as possible. For a fluid at rest ($\vec{u}$ = 0), equation (1) says that zero must be the most probable velocity, while the longer diagonal velocity vectors must be less probable than the shorter horizontal and vertical vectors. Velocities with the same magnitude must have the same probability, regardless of direction. The optimum probabilities turn out to be 4/9 for velocity zero, 1/9 for the four cardinal directions, and 1/36 for the diagonals. I’ll
denote these probabilities (or weights) by $w_i$:


$w_0 = \frac{4}{9}$    

$w_1=w_2=w_3=w_4 = \frac{1}{9}$

$w_5=w_6=w_7=w_8 = \frac{1}{36}$

In [4]:
#notice weights[0] represents w_0 = 4/9
weights = np.array([4/9,1/9,1/36,1/9,1/36,1/9,1/36,1/9,1/36]) # sums to 1

#### Streams and Collisions
The discrete map that results of the Lattice Boltzmann equation can be interpreted as the propagation and collision of particles.

Fundamentally, particles **stream** and **collide** evolving the density of the fluid $\rho(\vec{x},t)$ where $\vec{x}$ is the position and $t$ serves as time.

##### Streaming:

$\rho_i({\vec {x}}+{\vec {e}}_{i},t+\delta _{t})=\rho_i({\vec {x}},t)$

This means that the fluid density at point $\vec{x}$ and time $t$ will have flowed to the point $\vec{x} + \vec{e_i} $ by the time  $t + \delta_{t}$

##### Collision:
$\rho_i({\vec {x}},t+\delta _{t})=f_{i}({\vec {x}},t)+{\frac {f_{i}^{eq}({\vec {x}},t)-f_{i}({\vec {x}},t)}{\tau _{f}}}$

where $f_{i}^{eq}(\vec{x},t)$ is the equilibrium density along direction i at the current density there. The model assumes that the fluid locally relaxes to equilibrium over a characteristic timescale $\tau _{f}$ This timescale determines the kinematic viscosity, the larger it is, the larger is the kinematic viscosity.

#### The Lattice-Boltzmann Algorithm

In a lattice-Boltzmann simulation, the fundamental dynamical variables are **the nine different number densities, of molecules moving at the nine allowed velocities,at each lattice site.** 

In [5]:
# Initial Conditions NINE DIFFERENT NUMBER OF DENSITIES
F = np.ones((Ny,Nx,NL)) #* rho0 / NL
print(F.shape)
np.random.seed(42)

# Creating a right flow!
F += 0.01*np.random.randn(Ny,Nx,NL)
X, Y = np.meshgrid(range(Nx), range(Ny))
F[:,:,3] += 2 
rho = np.sum(F,2)
for i in idxs:
    F[:,:,i] *= rho0 / rho

(150, 300, 9)


Thus, your simulation will need nine two-dimensional arrays
of real numbers to represent these densities.

At any given time, at a given lattice site, these nine densities can have any
positive values. From these values you can then compute the total density, ρ, as
well as the x and y components of the average (that is, macroscopic) velocity, ux
and uy. And from these three macroscopic variables, you can compute what the
nine densities would be if the molecules at this site were in thermal equilibrium:


$F_i^{eq} = w_i \rho ( 1 + 3({v_i}\cdot{u}) + \frac{9}{2}({v_i}\cdot{u})^2 + \frac{3}{2}({u}\cdot{u})^2 )$

In [6]:
# Calculate fluid variables
rho = np.sum(F, axis = 2)
ux  = np.sum(F*cxs,axis = 2) / rho
uy  = np.sum(F*cys,axis = 2) / rho

# Apply Collision
#HINT u = (ux,uy) v_i = (cx,cy)
Feq = np.zeros(F.shape)
for i, cx, cy, w in zip(idxs, cxs, cys, weights):
    Feq[:,:,i] = rho * w * ( 1 + 3*(cx*ux+cy*uy)  + 9*(cx*ux+cy*uy)**2/2 - 3*(ux**2+uy**2)/2 )
#Collision
F += -(1.0/tau) * (F - Feq)


$\rho_i({\vec {x}},t+\delta _{t})=f_{i}({\vec {x}},t)+{\frac {f_{i}^{eq}({\vec {x}},t)-f_{i}({\vec {x}},t)}{\tau _{f}}}$

#### Puting everything together:

In [7]:
# Initial Conditions
F = np.ones((Ny,Nx,NL)) #* rho0 / NL
np.random.seed(42)
#Random perturbations.
F += 0.01*np.random.randn(Ny,Nx,NL)

#Flow to the right!
#We need to create an initial right flow
F[:,:,3] += 2
rho = np.sum(F,2)
for i in idxs:
    F[:,:,i] *= rho0 / rho
        
# Prep figure
def main(F):
    fig = plt.figure(figsize=(4,2), dpi=80) 
    with writer.saving(fig, "animation.mp4", dpi=200):
        for timestep in range(dt):
            #print(it)
            # For every of the 9 fluids, apply drift, np.roll()
            #the value Fᵢ is shifted over to the neighboring lattice site along the connection.
            for i, cx, cy in zip(idxs, cxs, cys):
                F[:,:,i] = np.roll(F[:,:,i], cx, axis=1)
                F[:,:,i] = np.roll(F[:,:,i], cy, axis=0)
            
            # Set reflective boundaries
            #bounce back the particles by swaping directions within our cylnder collisions.
            boundary = F[cylinder,:]
            boundary = boundary[:,[0,5,6,7,8,1,2,3,4]]
            boundary2 = F[cylinder2,:]

            # Calculate fluid variables
            #VORTICITY = DELTA x V
            rho = np.sum(F,axis = 2)
            ux  = np.sum(F*cxs, axis = 2) / rho
            uy  = np.sum(F*cys, axis = 2) / rho

            # Apply Collision
            Feq = np.zeros(F.shape)
            for i, cx, cy, w in zip(idxs, cxs, cys, weights):
                Feq[:,:,i] = rho * w * ( 1 + 3*(cx*ux+cy*uy)  + 9*(cx*ux+cy*uy)**2/2 - 3*(ux**2+uy**2)/2 )
            F += -(1.0/tau) * (F - Feq)
            
            # Apply boundary 
            F[cylinder,:] = boundary
            F[cylinder2,:] = boundary2

            if ((timestep % 10) == 0):
                plt.cla()
                ux[cylinder] = 0
                uy[cylinder] = 0
                #ux[cylinder2] = 0
                #uy[cylinder2] = 0
                #DIVIDE THE PARTICLES 1/2 and 1/2 this will keep track of the particle. based on direction
                vorticity = (np.roll(ux, -1, axis=0) - np.roll(ux, 1, axis=0)) - (np.roll(uy, -1, axis=1) - np.roll(uy, 1, axis=1))
                vorticity[cylinder] = 0
                #vorticity[cylinder2] = 0
                cmap = copy.copy(plt.cm.get_cmap("PiYG"))
                plt.imshow(vorticity, cmap='PiYG')
                #will keep the intensity of our cmap color
                plt.clim(-.1, .1)
                ax = plt.gca()
                plt.pause(0.001)
                writer.grab_frame()
            
    # Save figure
    plt.savefig('latticeboltzmann.png',dpi=240)
    plt.show()
    return 0

In [8]:
main(F)

0